In [1]:
import mitosheet
mitosheet.sheet(analysis_to_replay="id-nfkyumwmml")

In [2]:
from mitosheet.public.v3 import *; # Analysis Name:id-nfkyumwmml;
import pandas as pd
import numpy as np

# Imported train.csv, test.csv, test.csv
train = pd.read_csv(r'/Users/richardfarr/Documents/01 BUSINESS/01 DATA ANALYTICS/06 PROJECTS/01 Kaggle Competitions/Kaggle_Competitions/01 Titanic/data/train.csv')
test = pd.read_csv(r'/Users/richardfarr/Documents/01 BUSINESS/01 DATA ANALYTICS/06 PROJECTS/01 Kaggle Competitions/Kaggle_Competitions/01 Titanic/data/test.csv')
test_1 = pd.read_csv(r'/Users/richardfarr/Documents/01 BUSINESS/01 DATA ANALYTICS/06 PROJECTS/01 Kaggle Competitions/Kaggle_Competitions/01 Titanic/data/test.csv')

# add a column to the test dataframe called Survived and set as Null
test['Survived'] = pd.np.nan

# Reordered column Survived
test_columns = [col for col in test.columns if col != 'Survived']
test_columns.insert(1, 'Survived')
test = test[test_columns]

# create a new dataframe called combined by combining train and test dataframes
combined = pd.concat([train, test], ignore_index=True)

# create a column called title from the name column and extract common titles such as Mr, Mrs, Miss and others
combined['Title'] = combined['Name'].str.extract(' ([A-Za-z]+)\.', expand=False)
combined['Title'] = combined['Title'].replace(['Lady', 'Countess','Capt', 'Col','Don', 'Dr', 'Major', 'Rev', 'Sir', 'Jonkheer', 'Dona'], 'Other')
combined['Title'] = combined['Title'].replace('Mlle', 'Miss')
combined['Title'] = combined['Title'].replace('Ms', 'Miss')
combined['Title'] = combined['Title'].replace('Mme', 'Mrs')

# Filled NaN values in 1 columns in combined
combined.fillna({'Cabin': 'Unknown'}, inplace=True)

# Create a new column called cabin class that is based on the first letter of the Cabin column
combined['Cabin Class'] = combined['Cabin'].str[0]

# create a new column called group size that is 1 + SibSp + Parch
combined['group size'] = 1 + combined['SibSp'] + combined['Parch']

# create a new column called ticket_group_size based on the number of tickets sold with the name data
combined['ticket_group_size'] = combined.groupby('Ticket')['Name'].transform('count')

# create a column called Fare_adjusted that is Fare / ticket_group_size
combined['Fare_adjusted'] = combined['Fare'] / combined['ticket_group_size']

# create a column called fare_adjusted_decile that buckets Fare_adjusted into 10 equally sized buckets
combined['fare_adjusted_decile'] = pd.qcut(combined['Fare_adjusted'], q=10, labels=False)

# impute the missing Age values by using the mode of the age by Title
combined['Age'] = combined.groupby('Title')['Age'].transform(lambda x: x.fillna(x.mode()[0]))

# round the Age column to the nearest 0.1
combined['Age'] = combined['Age'].round(1)

# create a column called group_size_difference that is group_size - ticket_group_size
combined['group_size_difference'] = combined['group size'] - combined['ticket_group_size']

# Sorted Embarked in ascending order
combined = combined.sort_values(by='Embarked', ascending=True, na_position='first')

# create a train_cleaned from the combined dataframe where survived is either 0 or 1
train_cleaned = combined[(combined['Survived'] == 0) | (combined['Survived'] == 1)].copy()

# create a test cleaned dataframe from combined where Survived is NaN
test_cleaned = combined[combined['Survived'].isnull()]
test_cleaned.reset_index(drop=True, inplace=True)

# use a box cox transformation to convert age to a normally distributed variable
import scipy.stats as stats

combined['Age'], _ = stats.boxcox(combined['Age'])

# Sorted Ticket in ascending order
train = train.sort_values(by='Ticket', ascending=True, na_position='first')


/var/folders/5m/8p50g6vj6q18kpvx7v37b6zc0000gn/T/ipykernel_4286/3000530806.py:11: FutureWarning: The pandas.np module is deprecated and will be removed from pandas in a future version. Import numpy directly instead.
  test['Survived'] = pd.np.nan


In [3]:
import mitosheet
mitosheet.sheet(train_cleaned, analysis_to_replay="id-nnrzxnwozd")

In [4]:
from mitosheet.public.v3 import *; # Analysis Name:id-nnrzxnwozd;
# fill missing valued from embarked with the mode
train_cleaned['Embarked'].fillna(train_cleaned['Embarked'].mode()[0], inplace=True)

# Changed Survived to dtype bool
train_cleaned['Survived'] = train_cleaned['Survived'].fillna(False).astype('bool')

# Sorted Cabin Class in ascending order
train_cleaned = train_cleaned.sort_values(by='Cabin Class', ascending=True, na_position='first')
